In [1]:
import geopandas as gpd

In [85]:
# gdf = gpd.read_file("shapefiles/tl_2023_us_uac20/tl_2023_us_uac20.shp").rename(
gdf = gpd.read_file("shapefiles/cb_2018_us_ua10_500k/cb_2018_us_ua10_500k.shp").rename(
    columns={
        "UACE10": "urban area",
        "NAME10": "name",
    }
)
gdf

urban area      AFFGEOID10 GEOID10                       name LSAD10  \
0         88732  400C100US88732   88732                 Tucson, AZ     75   
1         01819  400C100US01819   01819                Alturas, CA     76   
2         22366  400C100US22366   22366          Davenport, IA--IL     75   
3         93322  400C100US93322   93322         Waynesboro, PA--MD     76   
4         02548  400C100US02548   02548                 Angola, IN     76   
...         ...             ...     ...                        ...    ...   
3596      57395  400C100US57395   57395                 Milton, DE     76   
3597      85390  400C100US85390   85390        Sugarmill Woods, FL     76   
3598      46639  400C100US46639   46639  Lake Conroe Eastshore, TX     76   
3599      15886  400C100US15886   15886               Checotah, OK     76   
3600      22933  400C100US22933   22933      De Funiak Springs, FL     76   

     UATYP10    ALAND10  AWATER10  \
0          U  915276150   2078695   
1          C    4933312     16517   
2          U  357345121  21444164   
3          C   45455957     88872   
4          C   23646957   3913803   
...      ...        ...       ...   
3596       C    3147288    167254   
3597       C   27203875         0   
3598       C   18747170     63639   
3599       C    3259478         0   
3600       C   17563989    691086   

                                               geometry  
0     MULTIPOLYGON (((-110.81345 32.11910, -110.7987...  
1     MULTIPOLYGON (((-120.54610 41.51264, -120.5459...  
2     MULTIPOLYGON (((-90.36678 41.53636, -90.36462 ...  
3     MULTIPOLYGON (((-77.50746 39.71577, -77.50605 ...  
4     MULTIPOLYGON (((-85.01157 41.59300, -85.00589 ...  
...                                                 ...  
3596  POLYGON ((-75.32719 38.77206, -75.31976 38.776...  
3597  MULTIPOLYGON (((-82.51716 28.75400, -82.51339 ...  
3598  MULTIPOLYGON (((-95.57872 30.40884, -95.57692 ...  
3599  POLYGON ((-95.53799 35.47168, -95.53998 35.472...  
3600  MULTIPOLYGON (((-86.13076 30.75629, -86.12938 ...  

[3601 rows x 9 columns]

In [86]:
gdf[gdf['urban area'] == "06868"]

urban area      AFFGEOID10 GEOID10      name LSAD10 UATYP10    ALAND10  \
469      06868  400C100US06868   06868  Bend, OR     75       U  102824264   

     AWATER10                                           geometry  
469    560560  MULTIPOLYGON (((-121.24345 44.05129, -121.2269...

In [4]:
from utilities import get_state_abbreviations_from_region, filter_by_states

In [6]:
import requests
import pandas as pd

In [7]:
import json
with open("private_info.json.private") as fp:
    api_key = json.load(fp)['census_api_key']

In [52]:
# api_key = 'your_api_key'

# Example API query for population data
url = f'https://api.census.gov/data/2019/acs/acs1?get=NAME,B01001_001E&for=us:*&key={api_key}'
# url = f'https://api.census.gov/data/2020/dec/sf1?get=P001001,NAME&for=urban+area:*&key={api_key}'
url = f"https://api.census.gov/data/2019/acs/acs1?get=NAME,B01003_001E&for=urban%20area:*&key={api_key}"

response = requests.get(url)
response

<Response [200]>

In [61]:
data = response.json()
data

[['NAME', 'B01003_001E', 'urban area'],
 ['Aberdeen--Bel Air South--Bel Air North, MD Urbanized Area (2010)',
  '222834',
  '00199'],
 ['Abilene, TX Urbanized Area (2010)', '110993', '00280'],
 ['Aguadilla--Isabela--San Sebastián, PR Urbanized Area (2010)',
  '260331',
  '00631'],
 ['Akron, OH Urbanized Area (2010)', '570375', '00766'],
 ['Albany, GA Urbanized Area (2010)', '89323', '00901'],
 ['Albany, OR Urbanized Area (2010)', '66405', '00955'],
 ['Albany--Schenectady, NY Urbanized Area (2010)', '590823', '00970'],
 ['Albuquerque, NM Urbanized Area (2010)', '762853', '01171'],
 ['Alexandria, LA Urbanized Area (2010)', '75835', '01279'],
 ['Allentown, PA--NJ Urbanized Area (2010)', '688658', '01495'],
 ['Alton, IL--MO Urbanized Area (2010)', '83705', '01765'],
 ['Altoona, PA Urbanized Area (2010)', '73374', '01792'],
 ['Amarillo, TX Urbanized Area (2010)', '202902', '01927'],
 ['Ames, IA Urbanized Area (2010)', '65864', '02062'],
 ['Anchorage, AK Urbanized Area (2010)', '248902', '02

In [76]:
population_df = pd.DataFrame(data[1:], columns=data[0]).drop(columns=['NAME']).rename(columns={"B01003_001E": "population"})
population_df

population urban area
0       222834      00199
1       110993      00280
2       260331      00631
3       570375      00766
4        89323      00901
..         ...        ...
433     236818      97750
434     363541      97831
435     124815      97939
436     137612      98020
437      79795      98182

[438 rows x 2 columns]

In [87]:
merged_gdf = gdf.merge(population_df, on='urban area', how='left')
merged_gdf.dropna()

urban area      AFFGEOID10 GEOID10                              name  \
0         88732  400C100US88732   88732                        Tucson, AZ   
2         22366  400C100US22366   22366                 Davenport, IA--IL   
6         15508  400C100US15508   15508  Charleston--North Charleston, SC   
7         13375  400C100US13375   13375                        Canton, OH   
8         97291  400C100US97291   97291                 Worcester, MA--CT   
...         ...             ...     ...                               ...   
3417      51175  400C100US51175   51175                      Longmont, CO   
3450      00970  400C100US00970   00970           Albany--Schenectady, NY   
3482      65863  400C100US65863   65863                       Orlando, FL   
3493      80389  400C100US80389   80389                       Seattle, WA   
3525      23527  400C100US23527   23527                Denver--Aurora, CO   

     LSAD10 UATYP10     ALAND10   AWATER10  \
0        75       U   915276150    2078695   
2        75       U   357345121   21444164   
6        75       U   759567710   29561590   
7        75       U   431157126    3070624   
8        75       U   787893340   33289002   
...     ...     ...         ...        ...   
3417     75       U    68006995    1856893   
3450     75       U   765902446   16203162   
3482     75       U  1546643103  142805447   
3493     75       U  2614905764  174194014   
3525     75       U  1726058510   38089345   

                                               geometry population  
0     MULTIPOLYGON (((-110.81345 32.11910, -110.7987...     883127  
2     MULTIPOLYGON (((-90.36678 41.53636, -90.36462 ...     281895  
6     MULTIPOLYGON (((-79.81082 32.77759, -79.80348 ...     645413  
7     MULTIPOLYGON (((-81.25737 40.87906, -81.25669 ...     277769  
8     MULTIPOLYGON (((-71.59616 42.17108, -71.59141 ...     516483  
...                                                 ...        ...  
3417  MULTIPOLYGON (((-105.00806 40.15929, -105.0049...     100146  
3450  MULTIPOLYGON (((-73.59799 42.65337, -73.59519 ...     590823  
3482  MULTIPOLYGON (((-81.10769 28.54499, -81.10569 ...    1792047  
3493  MULTIPOLYGON (((-121.92866 47.63873, -121.9268...    3530752  
3525  MULTIPOLYGON (((-104.71571 39.52160, -104.7154...    2709398  

[438 rows x 10 columns]

In [88]:
merged_gdf.to_file("big_data.geojson")

In [92]:
from utilities import *
my_states = get_state_abbreviations_from_region(["mid-atlantic"])
gdf1 = filter_by_states(merged_gdf, my_states)
gdf1

urban area      AFFGEOID10 GEOID10                          name LSAD10  \
3         93322  400C100US93322   93322            Waynesboro, PA--MD     76   
5         10891  400C100US10891   10891    Browns Mills--Fort Dix, NJ     76   
20        50338  400C100US50338   50338              Little Falls, NY     76   
69        89650  400C100US89650   89650  Uniontown--Connellsville, PA     75   
90        01792  400C100US01792   01792                   Altoona, PA     75   
...         ...             ...     ...                           ...    ...   
3557      66457  400C100US66457   66457                     Owego, NY     76   
3569      39835  400C100US39835   39835                 Honesdale, PA     76   
3572      43064  400C100US43064   43064              Jersey Shore, PA     76   
3585      64108  400C100US64108   64108                   Norwich, NY     76   
3588      97399  400C100US97399   97399                 Wurtsboro, NY     76   

     UATYP10    ALAND10  AWATER10  \
3          C   45455957     88872   
5          C   74394496   1510304   
20         C   10063551    372087   
69         U  100557008    497704   
90         U   96869930    164785   
...      ...        ...       ...   
3557       C   10114196    596877   
3569       C   10980811    502091   
3572       C   18112012    533116   
3585       C    8945718         0   
3588       C   11536502     69568   

                                               geometry population  ...  \
3     MULTIPOLYGON (((-77.50746 39.71577, -77.50605 ...        NaN  ...   
5     MULTIPOLYGON (((-74.47693 40.08094, -74.47640 ...        NaN  ...   
20    POLYGON ((-74.87997 43.02719, -74.87491 43.030...        NaN  ...   
69    MULTIPOLYGON (((-79.54857 40.03648, -79.54738 ...        NaN  ...   
90    MULTIPOLYGON (((-78.32161 40.61840, -78.31855 ...      73374  ...   
...                                                 ...        ...  ...   
3557  MULTIPOLYGON (((-76.22374 42.10624, -76.21875 ...        NaN  ...   
3569  MULTIPOLYGON (((-75.20413 41.52193, -75.20557 ...        NaN  ...   
3572  MULTIPOLYGON (((-77.18103 41.21085, -77.17735 ...        NaN  ...   
3585  MULTIPOLYGON (((-75.49261 42.51357, -75.49000 ...        NaN  ...   
3588  MULTIPOLYGON (((-74.45158 41.55911, -74.44970 ...        NaN  ...   

          GEOIDFQ STUSPS          NAME LSAD  MTFCC FUNCSTAT         ALAND  \
3     0400000US42     PA  Pennsylvania   00  G4000        A  115881839569   
5     0400000US34     NJ    New Jersey   00  G4000        A   19049183398   
20    0400000US36     NY      New York   00  G4000        A  122049078273   
69    0400000US42     PA  Pennsylvania   00  G4000        A  115881839569   
90    0400000US42     PA  Pennsylvania   00  G4000        A  115881839569   
...           ...    ...           ...  ...    ...      ...           ...   
3557  0400000US36     NY      New York   00  G4000        A  122049078273   
3569  0400000US42     PA  Pennsylvania   00  G4000        A  115881839569   
3572  0400000US42     PA  Pennsylvania   00  G4000        A  115881839569   
3585  0400000US36     NY      New York   00  G4000        A  122049078273   
3588  0400000US36     NY      New York   00  G4000        A  122049078273   

           AWATER     INTPTLAT      INTPTLON  
3      3397855215  +40.9046042  -077.8275233  
5      3532816229  +40.1072744  -074.6652012  
20    19256833049  +42.9133974  -075.5962723  
69     3397855215  +40.9046042  -077.8275233  
90     3397855215  +40.9046042  -077.8275233  
...           ...          ...           ...  
3557  19256833049  +42.9133974  -075.5962723  
3569   3397855215  +40.9046042  -077.8275233  
3572   3397855215  +40.9046042  -077.8275233  
3585  19256833049  +42.9133974  -075.5962723  
3588  19256833049  +42.9133974  -075.5962723  

[293 rows x 25 columns]

In [96]:
gdf1.columns

Index(['urban area', 'AFFGEOID10', 'GEOID10', 'name', 'LSAD10', 'UATYP10',
       'ALAND10', 'AWATER10', 'geometry', 'population', 'REGION', 'DIVISION',
       'STATEFP', 'STATENS', 'GEOID', 'GEOIDFQ', 'STUSPS', 'NAME', 'LSAD',
       'MTFCC', 'FUNCSTAT', 'ALAND', 'AWATER', 'INTPTLAT', 'INTPTLON'],
      dtype='object')

In [95]:
gdf1.explore()